In [1]:
import os
print(os.getcwd())

/workspaces/IC-RNA-2025/Peaks-dataset-article/redes-ensemble-s/mse_sup_newdt copy


In [2]:
import os
import pandas as pd
import numpy as np
from itertools import combinations, islice, permutations
from sklearn.metrics import r2_score
from random import shuffle

# Diretórios dos modelos
diretorio_25_model = "/workspaces/IC-RNA-2025/Peaks-dataset-article/redes-ensemble-s/mse_sup_newdt copy/25_model"
diretorio_1000_model = "/workspaces/IC-RNA-2025/Peaks-dataset-article/redes-ensemble-s/mse_sup_newdt copy/1000_model"

# Listagem dos arquivos
file_list_25_model = [os.path.join(diretorio_25_model, f) for f in os.listdir(diretorio_25_model) if f.endswith(".xlsx")]
file_list_1000_model = [os.path.join(diretorio_1000_model, f) for f in os.listdir(diretorio_1000_model) if f.endswith(".xlsx")]

# Função para cálculo de MSE usando 1000_model
def calcula_mse_sup(conjunto):
    df_list = [pd.read_excel(arquivo) for arquivo in conjunto]
    z_preds = [df['Z_pred'].values.reshape(-1, 1) for df in df_list]
    Z_pred_total = np.hstack(z_preds)
    Z_media = np.mean(Z_pred_total, axis=1, keepdims=True)

    df = pd.read_excel("1000_model/1000_model_40_9_1.xlsx")
    Z = df['Z'].values.reshape(-1, 1)

    mse_sup = np.mean((Z - Z_media) ** 2)
  
    r2_sup = r2_score(Z, Z_media)

    #print(f"mse: {mse}")
    return mse_sup, r2_sup

# Função para cálculo da diversidade usando 25_model
def diversity(conjunto):
    df_list = [pd.read_excel(arquivo) for arquivo in conjunto]
    z_preds = [df['Z_pred'].values.reshape(-1, 1) for df in df_list]

    df = pd.read_excel("25_model/25_model_40_9_1.xlsx")
    Z = df['Z'].values.reshape(-1, 1)

    Z_pred_total = np.hstack(z_preds)
    Z_media = np.mean(Z_pred_total, axis=1, keepdims=True)

    error1 = sum((Z - z_pred) ** 2 for z_pred in z_preds)
    error2 = sum((z_pred - Z_media) ** 2 for z_pred in z_preds)
    error = error1 + error2

    return np.mean(error.T)

# Função para cálculo de variância, viés e covariância usando 25_model
def mse_var_bias_covar(conjunto):
    df_list = [pd.read_excel(arquivo) for arquivo in conjunto]
    z_preds = [df['Z_pred'].values.reshape(-1, 1) for df in df_list]
    Z_pred_total = np.hstack(z_preds)
    Z_media = np.mean(Z_pred_total, axis=1, keepdims=True)

    df = pd.read_excel("25_model/25_model_40_9_1.xlsx")
    Z = df['Z'].values.reshape(-1, 1)

    var = [np.mean((z_pred - Z_media) ** 2) for z_pred in z_preds]
    var = np.mean(np.array(var))

    bias = np.mean((Z_media - Z) ** 2)

    M = 10  # número de redes
    cov_sum = 0
    for i in range(M):
        for j in range(M):
            if i != j:
                f_i = z_preds[i]
                f_j = z_preds[j]
                f_i_mean = np.mean(f_i)
                f_j_mean = np.mean(f_j)
                cov_ij = np.mean((f_i - f_i_mean) * (f_j - f_j_mean))
                cov_sum += cov_ij

    covar = cov_sum / (M * (M - 1))
    r2 = r2_score(Z, Z_media)

    return ( var, bias, covar, r2)

import os
import random

def filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto,
    pasta_destino,
    nome_pasta,
    limite=1000
):
    resultados = []

    # Carrega os nomes dos arquivos
    arquivos_25 = sorted([f for f in os.listdir(diretorio_25_model) if f.endswith(".xlsx")])
    arquivos_1000 = sorted([f for f in os.listdir(diretorio_1000_model) if f.endswith(".xlsx")])

    # Mapeia pelos sufixos
    nomes_25 = {
        f.replace("25_model_", ""): os.path.join(diretorio_25_model, f)
        for f in arquivos_25
    }
    nomes_1000 = {
        f.replace("1000_model_", ""): os.path.join(diretorio_1000_model, f)
        for f in arquivos_1000
    }

    # Garante apenas os nomes que existem nos dois diretórios
    nomes_comuns = sorted(set(nomes_25.keys()) & set(nomes_1000.keys()))

    if len(nomes_comuns) < tamanho_conjunto:
        raise ValueError("Poucos modelos sincronizados para o tamanho do conjunto.")

    # Pares sincronizados (tuple: 25_model_path, 1000_model_path)
    pares_sincronizados = [(nomes_25[n], nomes_1000[n]) for n in nomes_comuns]

    # Geração aleatória das combinações de índices, preservando a correspondência
    usadas = set()
    combinacoes_aleatorias = []

    while len(combinacoes_aleatorias) < limite:
        amostra = tuple(sorted(random.sample(range(len(pares_sincronizados)), tamanho_conjunto)))
        if amostra not in usadas:
            usadas.add(amostra)
            combinacoes_aleatorias.append(amostra)

    # Avalia cada combinação
    for count, combinacao_indices in enumerate(combinacoes_aleatorias, start=1):
        combinacao_25 = [pares_sincronizados[i][0] for i in combinacao_indices]
        combinacao_1000 = [pares_sincronizados[i][1] for i in combinacao_indices]

        print(f"\nCombinacao {count}:")
        print(f"25_model: {[os.path.basename(p) for p in combinacao_25]}")
        print(f"1000_model: {[os.path.basename(p) for p in combinacao_1000]}")

        mse, r2_sup = calcula_mse_sup(combinacao_1000)
        erro = diversity(combinacao_25)
        var, bias, covar, r2 = mse_var_bias_covar(combinacao_25)
        MSE_var_bias = var + bias**2

        resultado = {
            "Conjunto": combinacao_25,
            "MSE_sup": mse,
            "r2_sup": r2_sup,
            "Erro de Diversidade": erro,
            "r2": r2,
            "var": var,
            "bias": bias,
            "covar": covar,
            "MSE_var_bias": MSE_var_bias
        }
        resultados.append(resultado)

    salvar_resultados(resultados, pasta_destino, nome_pasta)
    return resultados



# Função para salvar todos os resultados de uma vez
def salvar_resultados(resultados, pasta_destino, nome_pasta):
    if not os.path.exists(pasta_destino):
        os.makedirs(pasta_destino)

    df = pd.DataFrame(resultados)
    caminho_arquivo = os.path.join(pasta_destino, nome_pasta)
    df.to_excel(caminho_arquivo, index=False)
    print(f"Todos os resultados salvos em: {caminho_arquivo}")

# Parâmetros
tamanho_conjunto = 10
pasta_destino = "resultados"

# Execução
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_permutations.xlsx",
    limite=10000
)



Combinacao 1:
25_model: ['25_model_10_9_0.xlsx', '25_model_18_81_3.xlsx', '25_model_22_8_9.xlsx', '25_model_25_7_6.xlsx', '25_model_2_9_5.xlsx', '25_model_2_9_7.xlsx', '25_model_34_6_0.xlsx', '25_model_40_9_1.xlsx', '25_model_9_9_8.xlsx', '25_model_9_9_9.xlsx']
1000_model: ['1000_model_10_9_0.xlsx', '1000_model_18_81_3.xlsx', '1000_model_22_8_9.xlsx', '1000_model_25_7_6.xlsx', '1000_model_2_9_5.xlsx', '1000_model_2_9_7.xlsx', '1000_model_34_6_0.xlsx', '1000_model_40_9_1.xlsx', '1000_model_9_9_8.xlsx', '1000_model_9_9_9.xlsx']

Combinacao 2:
25_model: ['25_model_13_9_5.xlsx', '25_model_13_9_6.xlsx', '25_model_18_91_0.xlsx', '25_model_18_91_1.xlsx', '25_model_20_81_4.xlsx', '25_model_22_9_18.xlsx', '25_model_24_91_11.xlsx', '25_model_34_6_1.xlsx', '25_model_6_5_6.xlsx', '25_model_9_9_9.xlsx']
1000_model: ['1000_model_13_9_5.xlsx', '1000_model_13_9_6.xlsx', '1000_model_18_91_0.xlsx', '1000_model_18_91_1.xlsx', '1000_model_20_81_4.xlsx', '1000_model_22_9_18.xlsx', '1000_model_24_91_11.xls

In [3]:
import os
import pandas as pd
import numpy as np
from itertools import combinations, islice
from sklearn.metrics import r2_score
from random import shuffle

# Diretórios dos modelos
diretorio_25_model = "/workspaces/IC-RNA-2025/Peaks-dataset-article/redes-ensemble-s/mse_sup_newdt copy/25_model"
diretorio_1000_model = "/workspaces/IC-RNA-2025/Peaks-dataset-article/redes-ensemble-s/mse_sup_newdt copy/1000_model"

# Listagem dos arquivos
file_list_25_model = [os.path.join(diretorio_25_model, f) for f in os.listdir(diretorio_25_model) if f.endswith(".xlsx")]
file_list_1000_model = [os.path.join(diretorio_1000_model, f) for f in os.listdir(diretorio_1000_model) if f.endswith(".xlsx")]

# Função para cálculo de MSE usando 1000_model
def calcula_mse_sup(conjunto):
    df_list = [pd.read_excel(arquivo) for arquivo in conjunto]
    z_preds = [df['Z_pred'].values.reshape(-1, 1) for df in df_list]
    Z_pred_total = np.hstack(z_preds)
    Z_media = np.mean(Z_pred_total, axis=1, keepdims=True)

    df = pd.read_excel("1000_model/1000_model_40_9_1.xlsx")
    Z = df['Z'].values.reshape(-1, 1)

    mse_sup = np.mean((Z - Z_media) ** 2)
  
    r2_sup = r2_score(Z, Z_media)

    #print(f"mse: {mse}")
    return mse_sup, r2_sup

# Função para cálculo da diversidade usando 25_model
def diversity(conjunto):
    df_list = [pd.read_excel(arquivo) for arquivo in conjunto]
    z_preds = [df['Z_pred'].values.reshape(-1, 1) for df in df_list]

    df = pd.read_excel("25_model/25_model_40_9_1.xlsx")
    Z = df['Z'].values.reshape(-1, 1)

    Z_pred_total = np.hstack(z_preds)
    Z_media = np.mean(Z_pred_total, axis=1, keepdims=True)

    error1 = sum((Z - z_pred) ** 2 for z_pred in z_preds)
    error2 = sum((z_pred - Z_media) ** 2 for z_pred in z_preds)
    error = error1 + error2

    return np.mean(error.T)

# Função para cálculo de variância, viés e covariância usando 25_model
def mse_var_bias_covar(conjunto):
    df_list = [pd.read_excel(arquivo) for arquivo in conjunto]
    z_preds = [df['Z_pred'].values.reshape(-1, 1) for df in df_list]
    Z_pred_total = np.hstack(z_preds)
    Z_media = np.mean(Z_pred_total, axis=1, keepdims=True)

    df = pd.read_excel("25_model/25_model_40_9_1.xlsx")
    Z = df['Z'].values.reshape(-1, 1)

    var = [np.mean((z_pred - Z_media) ** 2) for z_pred in z_preds]
    var = np.mean(np.array(var))

    bias = np.mean((Z_media - Z) ** 2)

    M = 10  # número de redes
    cov_sum = 0
    for i in range(M):
        for j in range(M):
            if i != j:
                f_i = z_preds[i]
                f_j = z_preds[j]
                f_i_mean = np.mean(f_i)
                f_j_mean = np.mean(f_j)
                cov_ij = np.mean((f_i - f_i_mean) * (f_j - f_j_mean))
                cov_sum += cov_ij

    covar = cov_sum / (M * (M - 1))
    r2 = r2_score(Z, Z_media)

    return ( var, bias, covar, r2)

import os
from random import shuffle
from itertools import islice

def filtrar_combinacoes_sincronizadas(diretorio_25_model, diretorio_1000_model, tamanho_conjunto, pasta_destino, nome_pasta, limite=1000):
    resultados = []

    # Carrega os nomes dos arquivos
    arquivos_25 = sorted([f for f in os.listdir(diretorio_25_model) if f.endswith(".xlsx")])
    arquivos_1000 = sorted([f for f in os.listdir(diretorio_1000_model) if f.endswith(".xlsx")])

    # Mapeia pelos sufixos
    nomes_25 = {
        f.replace("25_model_", ""): os.path.join(diretorio_25_model, f)
        for f in arquivos_25
    }
    nomes_1000 = {
        f.replace("1000_model_", ""): os.path.join(diretorio_1000_model, f)
        for f in arquivos_1000
    }

    # Garante apenas os nomes que existem nos dois diretórios
    nomes_comuns = sorted(set(nomes_25.keys()) & set(nomes_1000.keys()))

    if len(nomes_comuns) < tamanho_conjunto:
        raise ValueError("Poucos modelos sincronizados para o tamanho do conjunto.")

    # Pares sincronizados (tuple: 25_model_path, 1000_model_path)
    pares_sincronizados = [(nomes_25[n], nomes_1000[n]) for n in nomes_comuns]

    # Embaralha os pares para aleatoriedade
    shuffle(pares_sincronizados)

    # Divide os pares em blocos disjuntos de tamanho_conjunto
    total_blocos = len(pares_sincronizados) // tamanho_conjunto
    blocos_possiveis = min(total_blocos, limite)

    for count in range(blocos_possiveis):
        bloco = pares_sincronizados[count * tamanho_conjunto : (count + 1) * tamanho_conjunto]

        combinacao_25 = [par[0] for par in bloco]
        combinacao_1000 = [par[1] for par in bloco]

        print(f"\nConjunto {count + 1}:")
        print(f"25_model: {[os.path.basename(p) for p in combinacao_25]}")
        print(f"1000_model: {[os.path.basename(p) for p in combinacao_1000]}")

        mse, r2_sup = calcula_mse_sup(combinacao_1000)
        erro = diversity(combinacao_25)
        var, bias, covar, r2 = mse_var_bias_covar(combinacao_25)
        MSE_var_bias = var + bias**2

        resultado = {
            "Conjunto": combinacao_25,
            "MSE_sup": mse,
            "r2_sup": r2_sup,
            "Erro de Diversidade": erro,
            "r2": r2,
            "var": var,
            "bias": bias,
            "covar": covar,
            "MSE_var_bias": MSE_var_bias
        }
        resultados.append(resultado)

    salvar_resultados(resultados, pasta_destino, nome_pasta)
    return resultados


# Função para salvar todos os resultados de uma vez
def salvar_resultados(resultados, pasta_destino, nome_pasta):
    if not os.path.exists(pasta_destino):
        os.makedirs(pasta_destino)

    df = pd.DataFrame(resultados)
    caminho_arquivo = os.path.join(pasta_destino, nome_pasta)
    df.to_excel(caminho_arquivo, index=False)
    print(f"Todos os resultados salvos em: {caminho_arquivo}")

# Parâmetros
tamanho_conjunto = 10
pasta_destino = "resultados"

# Execução
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_sem_repetição_2.xlsx",
    limite=10
)
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_sem_repetição_3.xlsx",
    limite=10
)
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_sem_repetição_4.xlsx",
    limite=10
)
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_sem_repetição_5.xlsx",
    limite=10
)
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_sem_repetição_6.xlsx",
    limite=10
)
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_sem_repetição_7.xlsx",
    limite=10
)
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_sem_repetição_8.xlsx",
    limite=10
)
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_sem_repetição_9.xlsx",
    limite=10
)
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_sem_repetição_10.xlsx",
    limite=10
)
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_sem_repetição_11.xlsx",
    limite=10
)



Conjunto 1:
25_model: ['25_model_18_91_8.xlsx', '25_model_24_91_8.xlsx', '25_model_24_6_3.xlsx', '25_model_18_8_1.xlsx', '25_model_22_9_18.xlsx', '25_model_18_81_0.xlsx', '25_model_30_7_6.xlsx', '25_model_2_9_0.xlsx', '25_model_20_81_4.xlsx', '25_model_18_91_6.xlsx']
1000_model: ['1000_model_18_91_8.xlsx', '1000_model_24_91_8.xlsx', '1000_model_24_6_3.xlsx', '1000_model_18_8_1.xlsx', '1000_model_22_9_18.xlsx', '1000_model_18_81_0.xlsx', '1000_model_30_7_6.xlsx', '1000_model_2_9_0.xlsx', '1000_model_20_81_4.xlsx', '1000_model_18_91_6.xlsx']

Conjunto 2:
25_model: ['25_model_12_6_0.xlsx', '25_model_20_81_0.xlsx', '25_model_9_9_4.xlsx', '25_model_22_9_19.xlsx', '25_model_20_8_1.xlsx', '25_model_18_91_5.xlsx', '25_model_9_9_1.xlsx', '25_model_22_9_14.xlsx', '25_model_34_6_0.xlsx', '25_model_6_5_6.xlsx']
1000_model: ['1000_model_12_6_0.xlsx', '1000_model_20_81_0.xlsx', '1000_model_9_9_4.xlsx', '1000_model_22_9_19.xlsx', '1000_model_20_8_1.xlsx', '1000_model_18_91_5.xlsx', '1000_model_9_9_1

KeyboardInterrupt: 

In [ ]:
import os
import pandas as pd
import numpy as np
from itertools import combinations, islice
from sklearn.metrics import r2_score
from random import shuffle
from random import sample


# Diretórios dos modelos
diretorio_25_model = "/workspaces/IC-RNA-2025/Peaks-dataset-article/redes-ensemble-s/mse_sup_newdt copy/25_model"
diretorio_1000_model = "/workspaces/IC-RNA-2025/Peaks-dataset-article/redes-ensemble-s/mse_sup_newdt copy/1000_model"

# Listagem dos arquivos
file_list_25_model = [os.path.join(diretorio_25_model, f) for f in os.listdir(diretorio_25_model) if f.endswith(".xlsx")]
file_list_1000_model = [os.path.join(diretorio_1000_model, f) for f in os.listdir(diretorio_1000_model) if f.endswith(".xlsx")]

# Função para cálculo de MSE usando 1000_model
def calcula_mse_sup(conjunto):
    df_list = [pd.read_excel(arquivo) for arquivo in conjunto]
    z_preds = [df['Z_pred'].values.reshape(-1, 1) for df in df_list]
    Z_pred_total = np.hstack(z_preds)
    Z_media = np.mean(Z_pred_total, axis=1, keepdims=True)

    df = pd.read_excel("1000_model/1000_model_40_9_1.xlsx")
    Z = df['Z'].values.reshape(-1, 1)

    mse_sup = np.mean((Z - Z_media) ** 2)
  
    r2_sup = r2_score(Z, Z_media)

    #print(f"mse: {mse}")
    return mse_sup, r2_sup

# Função para cálculo da diversidade usando 25_model
def diversity(conjunto):
    df_list = [pd.read_excel(arquivo) for arquivo in conjunto]
    z_preds = [df['Z_pred'].values.reshape(-1, 1) for df in df_list]

    df = pd.read_excel("25_model/25_model_40_9_1.xlsx")
    Z = df['Z'].values.reshape(-1, 1)

    Z_pred_total = np.hstack(z_preds)
    Z_media = np.mean(Z_pred_total, axis=1, keepdims=True)

    error1 = sum((Z - z_pred) ** 2 for z_pred in z_preds)
    error2 = sum((z_pred - Z_media) ** 2 for z_pred in z_preds)
    error = error1 + error2

    return np.mean(error.T)

# Função para cálculo de variância, viés e covariância usando 25_model
def mse_var_bias_covar(conjunto):
    df_list = [pd.read_excel(arquivo) for arquivo in conjunto]
    z_preds = [df['Z_pred'].values.reshape(-1, 1) for df in df_list]
    Z_pred_total = np.hstack(z_preds)
    Z_media = np.mean(Z_pred_total, axis=1, keepdims=True)

    df = pd.read_excel("25_model/25_model_40_9_1.xlsx")
    Z = df['Z'].values.reshape(-1, 1)

    var = [np.mean((z_pred - Z_media) ** 2) for z_pred in z_preds]
    var = np.mean(np.array(var))

    bias = np.mean((Z_media - Z) ** 2)

    M = 10  # número de redes
    cov_sum = 0
    for i in range(M):
        for j in range(M):
            if i != j:
                f_i = z_preds[i]
                f_j = z_preds[j]
                f_i_mean = np.mean(f_i)
                f_j_mean = np.mean(f_j)
                cov_ij = np.mean((f_i - f_i_mean) * (f_j - f_j_mean))
                cov_sum += cov_ij

    covar = cov_sum / (M * (M - 1))
    r2 = r2_score(Z, Z_media)

    return ( var, bias, covar, r2)


def filtrar_combinacoes_sincronizadas(diretorio_25_model, diretorio_1000_model, tamanho_conjunto, pasta_destino, nome_pasta, limite=None):
    resultados = []

    # Carrega os nomes dos arquivos
    arquivos_25 = sorted([f for f in os.listdir(diretorio_25_model) if f.endswith(".xlsx")])
    arquivos_1000 = sorted([f for f in os.listdir(diretorio_1000_model) if f.endswith(".xlsx")])

    # Mapeia pelos sufixos
    nomes_25 = {
        f.replace("25_model_", ""): os.path.join(diretorio_25_model, f)
        for f in arquivos_25
    }
    nomes_1000 = {
        f.replace("1000_model_", ""): os.path.join(diretorio_1000_model, f)
        for f in arquivos_1000
    }

    # Garante apenas os nomes que existem nos dois diretórios
    nomes_comuns = sorted(set(nomes_25.keys()) & set(nomes_1000.keys()))

    if len(nomes_comuns) < tamanho_conjunto:
        raise ValueError("Poucos modelos sincronizados para o tamanho do conjunto.")

    # Pares sincronizados (tuple: 25_model_path, 1000_model_path)
    pares_sincronizados = [(nomes_25[n], nomes_1000[n]) for n in nomes_comuns]


    # Gera todas as combinações possíveis de índices e embaralha
    todas_combinacoes = list(combinations(range(len(pares_sincronizados)), tamanho_conjunto))
    shuffle(todas_combinacoes)

    indices = list(combinations(range(1000), 10))  # N = total de redes, k = tamanho do conjunto
    combinacoes_aleatorias = sample(indices, k=len(indices))  # ou limitar o número de amostras

    for count, combinacao_indices in enumerate(combinacoes_aleatorias, start=1):
        combinacao_25 = [pares_sincronizados[i][0] for i in combinacao_indices]
        combinacao_1000 = [pares_sincronizados[i][1] for i in combinacao_indices]

        print(f"\nCombinacao {count}:")
        print(f"25_model: {[os.path.basename(p) for p in combinacao_25]}")
        print(f"1000_model: {[os.path.basename(p) for p in combinacao_1000]}")

        mse, r2_sup = calcula_mse_sup(combinacao_1000)
        erro = diversity(combinacao_25)
        var, bias, covar, r2 = mse_var_bias_covar(combinacao_25)
        MSE_var_bias = var + bias**2

        resultado = {
            "Conjunto": combinacao_25,
            "MSE_sup": mse,
            "r2_sup": r2_sup,
            "Erro de Diversidade": erro,
            "r2": r2,
            "var": var,
            "bias": bias,
            "covar": covar,
            "MSE_var_bias": MSE_var_bias
        }
        resultados.append(resultado)

    salvar_resultados(resultados, pasta_destino, nome_pasta)
    return resultados

# Função para salvar todos os resultados de uma vez
def salvar_resultados(resultados, pasta_destino, nome_pasta):
    if not os.path.exists(pasta_destino):
        os.makedirs(pasta_destino)

    df = pd.DataFrame(resultados)
    caminho_arquivo = os.path.join(pasta_destino, nome_pasta)
    df.to_excel(caminho_arquivo, index=False)
    print(f"Todos os resultados salvos em: {caminho_arquivo}")

# Parâmetros
tamanho_conjunto = 10
pasta_destino = "resultados"

# Execução
resultados = filtrar_combinacoes_sincronizadas(
    diretorio_25_model,
    diretorio_1000_model,
    tamanho_conjunto=10,
    pasta_destino="resultados",
    nome_pasta= "todos_resultados_2.xlsx",
    limite=1000
)


: 